In [1]:
import pandas as pd
import akshare as ak
import os
from pathlib import Path
from loguru import logger
import sys

# 配置日志（使用相对路径，基于当前工作目录）
logger.add("Log/downloadHS300.log", encoding="utf-8")

# 获取当前工作目录（替代 __file__）
current_dir = Path.cwd()

# 设置数据路径
start_date = '20150101'
test_path = current_dir / "DownLoadData"
test_path.mkdir(exist_ok=True, parents=True)

# 添加当前目录到搜索路径
sys.path.append(str(current_dir))

# 导入自定义模块
from EnumData import OriginalNameUnified as UnifiedName

# 后续函数定义和逻辑保持不变...

def process_stock_data(df, stock_code, file_path):
    """处理股票数据，清除包含负数的行"""
    try:
        # 确保日期列存在并设置为索引
        if 'Date' not in df.columns:
            logger.error(f"数据中没有找到 'Date' 列: {stock_code}")
            return None
            
        df.set_index('Date', inplace=True)

        # 查找价格列中的负数
        price_columns = ['Open', 'Close', 'High', 'Low']
        df_negative = df[(df[price_columns] < 0).any(axis=1)]

        # 如果有负数，从最后一个负数之后开始保留数据
        if not df_negative.empty:
            last_negative_date = df_negative.index[-1]
            logger.warning(f"找到负数数据，股票代码: {stock_code}, 最后一个负数日期: {last_negative_date}")
            
            # 获取最后一个负数的位置
            position = df.index.get_loc(last_negative_date)
            
            # 如果有后续数据，保留后续数据
            if position + 1 < len(df):
                next_date = df.index[position + 1]
                df_cleaned = df.loc[next_date:]
                logger.info(f"保留从 {next_date} 开始的数据")
            else:
                logger.warning(f"没有负数之后的数据: {stock_code}")
                return None
        else:
            logger.info(f"没有找到负数数据: {stock_code}")
            df_cleaned = df.copy()

        # 保存处理后的数据
        if not df_cleaned.empty:
            file_name = file_path / f"{stock_code}.csv"
            df_cleaned.to_csv(file_name, encoding="utf-8-sig")
            logger.info(f"数据保存成功: {file_name}")
            return df_cleaned
        else:
            logger.warning(f"处理后的数据为空: {stock_code}")
            return None

    except Exception as e:
        logger.error(f"处理数据时出错: {stock_code}, 错误: {str(e)}")
        return None

def getStockDataByIndex(stock_code, file_path):
    """获取单只股票的数据并处理"""
    try:
        logger.info(f"开始获取股票数据: {stock_code}")
        
        # 获取股票数据
        df = ak.stock_zh_a_hist(symbol=stock_code, period="daily", adjust="qfq", start_date=start_date)
        
        # 重命名列名
        df.rename(columns=UnifiedName.column_mapping_akshare, inplace=True)
        
        # 处理数据
        return process_stock_data(df, stock_code, file_path)
        
    except Exception as e:
        logger.error(f"获取股票数据时出错: {stock_code}, 错误: {str(e)}")
        return None

def getHS300StockIndex(store_path=None):
    """获取沪深300成分股数据"""
    store_path = store_path or (current_dir.parent / "DownLoadData" / "HS300")
    store_path.mkdir(exist_ok=True, parents=True)
    
    logger.info("开始获取沪深300成分股数据")
    
    try:
        # 获取沪深300成分股列表
        csi_300_df = ak.index_stock_cons(index="000300")
        
        # 遍历成分股获取数据
        for _, row in csi_300_df.iterrows():
            stock_code = row["品种代码"]
            getStockDataByIndex(stock_code, store_path)
            
        logger.info(f"沪深300成分股数据获取完成，共 {len(csi_300_df)} 只股票")
            
    except Exception as e:
        logger.error(f"获取沪深300成分股列表时出错: {str(e)}")

def getAllStockDataFromA(store_path=None):
    """获取所有A股股票数据"""
    store_path = store_path or (current_dir.parent / "DownLoadData" / "AllAStocks")
    store_path.mkdir(exist_ok=True, parents=True)
    
    logger.info("开始获取所有A股股票数据")
    
    try:
        # 获取A股股票列表
        stock_info_df = ak.stock_info_a_code_name()
        
        # 遍历所有股票获取数据
        total_stocks = len(stock_info_df)
        for i, (_, row) in enumerate(stock_info_df.iterrows()):
            stock_code = row["code"]
            logger.info(f"正在获取第 {i+1}/{total_stocks} 只股票: {stock_code}")
            getStockDataByIndex(stock_code, store_path)
            
        logger.info(f"所有A股股票数据获取完成，共 {total_stocks} 只股票")
            
    except Exception as e:
        logger.error(f"获取A股股票列表时出错: {str(e)}")

if __name__ == '__main__':
    logger.info("开始执行股票数据下载程序")
    getHS300StockIndex(test_path / "HS300")
    getAllStockDataFromA(test_path / "AllAStocks")
    logger.info("程序执行完成")

2025-05-26 20:33:13.895 | INFO     | __main__:<module>:138 - 开始执行股票数据下载程序
2025-05-26 20:33:13.895 | INFO     | __main__:getHS300StockIndex:98 - 开始获取沪深300成分股数据
2025-05-26 20:33:13.896 | ERROR    | __main__:getHS300StockIndex:112 - 获取沪深300成分股列表时出错: index_stock_cons() got an unexpected keyword argument 'index'
2025-05-26 20:33:13.896 | INFO     | __main__:getAllStockDataFromA:119 - 开始获取所有A股股票数据


  0%|          | 0/14 [00:00<?, ?it/s]

2025-05-26 20:33:20.181 | INFO     | __main__:getAllStockDataFromA:129 - 正在获取第 1/5415 只股票: 000001
2025-05-26 20:33:20.183 | INFO     | __main__:getStockDataByIndex:78 - 开始获取股票数据: 000001
2025-05-26 20:33:20.558 | INFO     | __main__:process_stock_data:58 - 没有找到负数数据: 000001
2025-05-26 20:33:20.569 | INFO     | __main__:process_stock_data:65 - 数据保存成功: d:\ifindata\第一次小组作业\DownLoadData\AllAStocks\000001.csv
2025-05-26 20:33:20.570 | INFO     | __main__:getAllStockDataFromA:129 - 正在获取第 2/5415 只股票: 000002
2025-05-26 20:33:20.570 | INFO     | __main__:getStockDataByIndex:78 - 开始获取股票数据: 000002
2025-05-26 20:33:22.097 | INFO     | __main__:process_stock_data:58 - 没有找到负数数据: 000002
2025-05-26 20:33:22.107 | INFO     | __main__:process_stock_data:65 - 数据保存成功: d:\ifindata\第一次小组作业\DownLoadData\AllAStocks\000002.csv
2025-05-26 20:33:22.107 | INFO     | __main__:getAllStockDataFromA:129 - 正在获取第 3/5415 只股票: 000004
2025-05-26 20:33:22.108 | INFO     | __main__:getStockDataByIndex:78 - 开始获取股票数据: 000004
20